In [7]:
import pandas as pd
import numpy as np
import pandas_datareader.data as pdr
import yfinance as yf
import datetime as dt
import matplotlib.pyplot as plt
import scipy.optimize as sc
from scipy.stats import norm
import plotly.express as px
import plotly.graph_objects as go

In [8]:
def change(close, mean):
    last = close[-1]
    chg = mean/last - 1
    return chg

### Optimization

In [9]:
def get_data(stock_list, start, end):
    stock_list.sort()
    data = pdr.get_data_yahoo(stock_list, start, end)
    return data['Close']
def stock_performance(close):
    returns = close.pct_change()
    mean_returns = returns.mean()
    cov = returns.cov()
    return mean_returns, cov

def portfolio_performance(W, mean_returns, cov):
    W = np.asarray(W)
    portfolio_returns = (np.dot(W, mean_returns) * 252)
    portfolio_risk = np.sqrt(W.T @ cov @ W) * np.sqrt(252)
    return portfolio_returns, portfolio_risk  

############################
def negative_sharpe_ratio(W, mean_returns, cov, risk_free_rate):
    portfolio_return, portfolio_risk = portfolio_performance(W, mean_returns, cov)
    neg_sharpe_ratio = -(portfolio_return - risk_free_rate)/portfolio_risk
    return neg_sharpe_ratio

def optimize_portfolio(mean_returns, cov, upper_bound, risk_free_rate):
    """
    returns
    -------
    sharpe_ratio, optimal_weights
    """
    #assign random weights
    np.random.seed(1)
    W = np.random.random(len(mean_returns))
    W = [weight/ np.sum(W) for weight in W]
    
    #add bounds
    bound = (0,upper_bound)
    bounds = tuple(bound for w in range(len(W)))
    
    #constraint 
    def constraint(W):
        return np.sum(W) - 1
    constraint_set = [{'type': 'eq', 'fun': constraint}]
    
    #minimize negative SharpeRatio
    result = sc.minimize(negative_sharpe_ratio,
                        W,
                        args=(mean_returns, cov, risk_free_rate),
                        method='SLSQP',
                        bounds= bounds,
                        constraints=constraint_set)
    neg_sharpe_ratio, optimal_weights = result['fun'], result['x'].round(4)             
    return -neg_sharpe_ratio, optimal_weights   


######################
def minimum_risk_portfolio(mean_returns, cov, upper_bound, risk_free_rate):
    """
    returns
    -------
    sharpe_ratio, optimal_weights"""
     #assign random weights
    np.random.seed(1)
    W = np.random.random(len(mean_returns))
    W = [weight/ np.sum(W) for weight in W]

    #add bounds
    bound = (0,upper_bound)
    bounds = tuple(bound for w in range(len(W)))

    #constraint 
    def constraint(W):
        return np.sum(W) - 1
    constraint_set = [{'type': 'eq', 'fun': constraint}]
    
    def portfolio_variance(W,cov):
        return (np.sqrt(W.T @ cov @ W) * np.sqrt(252))

    result = sc.minimize(portfolio_variance,
                        W,
                        args = (cov),
                        bounds = bounds,
                        constraints = constraint_set,
                        method = 'SLSQP')

    sharpe_ratio, optimal_weights = result['fun'], result['x'].round(4)
    return -sharpe_ratio, optimal_weights


### Efficient market frontier

In [10]:
def simulate_portfolios(stock_list, start, end, simulations = 1000):
    
    close = get_data(stock_list, start, end)
    mean_returns, cov = stock_performance(close)
    
    returns = []
    risk = []
    weights = []
    for p in range(simulations):
        W = np.random.random(len(stock_list))
        W = W / np.sum(W)
        weights.append(W)
        
        portfolio_returns, portfolio_risk = portfolio_performance(W, mean_returns, cov)
        returns.append(portfolio_returns)
        risk.append(portfolio_risk)

    portfolios_weights = pd.DataFrame(weights, columns= stock_list)
    
    portfolios = pd.concat([pd.DataFrame({'Returns': returns, 'Risk': risk,}), portfolios_weights], axis = 1)
    return portfolios

def plot_EF(data,
            mean_returns,
            cov,
            stock_list,
            upper_bound,
            risk_free_rate,
            start,
            end,
            simulations = 10000):
            
    portfolios = simulate_portfolios(stock_list, start, end, simulations)
    
    #portfolios    
    fig = px.scatter(portfolios, portfolios['Risk'], portfolios['Returns'], hover_data=stock_list)
    
    #minimum varaince portfolio
    _, optimal_weights = minimum_risk_portfolio(mean_returns, cov, upper_bound, risk_free_rate)
    minimum_risk_portfolio_return, minimum_risk_portfolio_risk = portfolio_performance(optimal_weights, mean_returns, cov)
    #plot
    fig.add_trace(go.Scatter(x = [minimum_risk_portfolio_risk], y = [minimum_risk_portfolio_return],
                            mode = 'markers',
                            marker_symbol = 'star',
                            marker_size = 10,
                            marker = {'color' : 'red'}))

    #maximum sharpe ratio portfolio
    _, optimal_weights = optimize_portfolio(mean_returns, cov,upper_bound, risk_free_rate)
    optimum_portfolio_returns, optimum_portfolio_risk = portfolio_performance(optimal_weights, mean_returns, cov)
    #plot
    fig.add_trace(go.Scatter(x=[optimum_portfolio_risk], y=[optimum_portfolio_returns], mode = 'markers',
                         marker_symbol = 'star',
                         marker_size = 10,
                         marker = {'color' : 'red'}))
    fig.show() 

### Random walk simulation

In [11]:
def MC(close, steps, simulations, random_seed):
    daily_returns = np.log(1 + close.pct_change())
    mu = np.mean(daily_returns)
    var = np.var(daily_returns)
    sigma = np.std(daily_returns)
    drift = mu - 0.5*var

    returns = np.exp(drift + sigma * norm.ppf(np.random.rand(steps, simulations)))
    np.random.seed(random_seed)
    sims = np.zeros((steps, simulations))
    sims[0] = close.iloc[-1]

    for step in range(1,steps):
        sims[step] = sims[step-1] * returns[step]
    return sims


def monteCarlo(close, steps, simulations, random_seed):

    sims = MC(close=close, steps=steps, simulations=simulations, random_seed=random_seed)
    mcmean = np.mean(sims[-1])
    mcvar = np.var(sims[-1])
    return mcmean, mcvar 

In [14]:
def main(upper_bound=0.2, monte_carlo = False, steps = 90):
    """
    Paramters:
    ----------
    upper_bound: specifies upper bound for portfolio weights
    monte_carlo: whether to use monte carlo simulation to model stock price
    steps: number of days simualted in when using monte carlo
    """
    
    # Stock list
    stock_list = ['uvxy','SPY','TLT', 'GLD', 'QQQ', 'XLRE', 'XLB', 'XLY', 'XLU','XLP', 'XLF']
    
    #time period
    end = dt.datetime.now()
    start = end - dt.timedelta(720)
    

    #bug fix
    yf.pdr_override()
    
    #get stock qoutes
    close = get_data(stock_list, start, end)

    mean_returns, cov = stock_performance(close)
    
    if monte_carlo: 
        steps = steps
        simulations = 10000  
        random_seed = 1
        mean_returns = []
        for i in range(close.shape[1]):
            c = close.iloc[:,i]
            mcmean, mcvar = monteCarlo(close=c, steps=steps,simulations=simulations,random_seed=random_seed)
            mean_returns.append(change(close=c, mean=mcmean))
        mean_returns = np.array(mean_returns)
    risk_free_rate = 0.04    
    #minimum variance porfolio    
    SR, optimal_weights = minimum_risk_portfolio(mean_returns, cov, upper_bound, risk_free_rate)
    portfolio_returns, portfolio_risk = portfolio_performance(optimal_weights, mean_returns, cov)

    print(f'Expected return: {portfolio_returns.round(3)}, Risk: {portfolio_risk.round(3)} with Sharpe Ratio:{SR.round(3)}\noptimal weights:')
    print(f'{stock_list}\n{optimal_weights}')
    print('\n--------------\n')

    #maximum Sharpe Ratio portfolio
    SR, optimal_weights = optimize_portfolio(mean_returns, cov, upper_bound, risk_free_rate)
    portfolio_returns, portfolio_risk = portfolio_performance(optimal_weights, mean_returns, cov)

    print(f'Expected return: {portfolio_returns.round(3)}, Risk: {portfolio_risk.round(3)} with Sharpe Ratio:{SR.round(3)}\noptimal weights:')
    print(f'{stock_list}\n{optimal_weights}')
    

    
    
    plot_EF(close,
            mean_returns,
            cov,
            stock_list,
            upper_bound,
            risk_free_rate,
            start,
            end,
            simulations = 10000)

main()

[*********************100%***********************]  11 of 11 completed
Expected return: -0.06, Risk: 0.084 with Sharpe Ratio:-0.084
optimal weights:
['GLD', 'QQQ', 'SPY', 'TLT', 'XLB', 'XLF', 'XLP', 'XLRE', 'XLU', 'XLY', 'uvxy']
[0.2    0.     0.2    0.1687 0.0732 0.     0.1581 0.2    0.     0.
 0.    ]

--------------

Expected return: 0.041, Risk: 0.139 with Sharpe Ratio:0.008
optimal weights:
['GLD', 'QQQ', 'SPY', 'TLT', 'XLB', 'XLF', 'XLP', 'XLRE', 'XLU', 'XLY', 'uvxy']
[0.2 0.  0.  0.  0.  0.2 0.2 0.2 0.  0.2 0. ]
[*********************100%***********************]  11 of 11 completed
